In [11]:
from IPython.core.display import HTML
import numpy as np
from scipy.sparse import diags
from scipy.sparse.linalg import spsolve
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
import numba
from scipy.interpolate import RectBivariateSpline
from scipy.ndimage import maximum_filter

# Numba optimized functions for costly computations
@numba.jit(nopython=True)
def compute_christoffel_symbols(gamma_xx, gamma_xy, gamma_yy, dx, dy):
    """Compute Christoffel symbols using Numba"""
    nx, ny = gamma_xx.shape
    
    # Preallocate arrays for derivatives
    gamma_xx_dx = np.zeros_like(gamma_xx)
    gamma_xy_dx = np.zeros_like(gamma_xx)
    gamma_yy_dx = np.zeros_like(gamma_xx)
    gamma_xx_dy = np.zeros_like(gamma_xx)
    gamma_xy_dy = np.zeros_like(gamma_xx)
    gamma_yy_dy = np.zeros_like(gamma_xx)
    
    # Compute derivatives using finite differences
    for i in range(1, nx-1):
        for j in range(ny):
            gamma_xx_dx[i,j] = (gamma_xx[i+1,j] - gamma_xx[i-1,j]) / (2*dx)
            gamma_xy_dx[i,j] = (gamma_xy[i+1,j] - gamma_xy[i-1,j]) / (2*dx)
            gamma_yy_dx[i,j] = (gamma_yy[i+1,j] - gamma_yy[i-1,j]) / (2*dx)
            
    for i in range(nx):
        for j in range(1, ny-1):
            gamma_xx_dy[i,j] = (gamma_xx[i,j+1] - gamma_xx[i,j-1]) / (2*dy)
            gamma_xy_dy[i,j] = (gamma_xy[i,j+1] - gamma_xy[i,j-1]) / (2*dy)
            gamma_yy_dy[i,j] = (gamma_yy[i,j+1] - gamma_yy[i,j-1]) / (2*dy)
    
    # Compute determinant and inverse metric components
    det = gamma_xx * gamma_yy - gamma_xy**2
    gamma_xx_inv = gamma_yy / det
    gamma_xy_inv = -gamma_xy / det
    gamma_yy_inv = gamma_xx / det
    
    # Compute Christoffel symbols
    christ_xxx = 0.5 * gamma_xx_dx
    christ_xxy = 0.5 * (gamma_xy_dx + gamma_xx_dy)
    christ_xyy = 0.5 * (gamma_yy_dx + 2*gamma_xy_dy)
    christ_yyy = 0.5 * gamma_yy_dy
    
    return christ_xxx, christ_xxy, christ_xyy, christ_yyy

@numba.jit(nopython=True)
def evolve_fields(chi, gamma_xx, gamma_xy, gamma_yy, K, A_xx, A_xy, A_yy, 
                 alpha, beta_x, beta_y, dx, dy, dt):
    """Evolve BSSN fields one timestep using Numba"""
    nx, ny = chi.shape
    
    # Preallocate arrays for new values
    chi_new = np.copy(chi)
    gamma_xx_new = np.copy(gamma_xx)
    gamma_xy_new = np.copy(gamma_xy)
    gamma_yy_new = np.copy(gamma_yy)
    K_new = np.copy(K)
    
    # Compute derivatives
    for i in range(1, nx-1):
        for j in range(1, ny-1):
            # Compute chi derivatives
            chi_dx = (chi[i+1,j] - chi[i-1,j]) / (2*dx)
            chi_dy = (chi[i,j+1] - chi[i,j-1]) / (2*dy)
            
            # Compute beta derivatives
            beta_x_dx = (beta_x[i+1,j] - beta_x[i-1,j]) / (2*dx)
            beta_y_dy = (beta_y[i,j+1] - beta_y[i,j-1]) / (2*dy)
            
            # Evolution equation for chi
            chi_dt = (2.0/3.0) * chi[i,j] * (alpha[i,j] * K[i,j] - beta_x_dx - beta_y_dy)
            
            # Evolution equations for conformal metric
            gamma_xx_dt = -2 * alpha[i,j] * A_xx[i,j]
            gamma_xy_dt = -2 * alpha[i,j] * A_xy[i,j]
            gamma_yy_dt = -2 * alpha[i,j] * A_yy[i,j]
            
            # Evolution equation for K
            K_dt = (alpha[i,j] * (A_xx[i,j]**2 + 2*A_xy[i,j]**2 + A_yy[i,j]**2) -
                   alpha[i,j] * K[i,j]**2/3)
            
            # Update fields
            chi_new[i,j] = chi[i,j] + dt * chi_dt
            gamma_xx_new[i,j] = gamma_xx[i,j] + dt * gamma_xx_dt
            gamma_xy_new[i,j] = gamma_xy[i,j] + dt * gamma_xy_dt
            gamma_yy_new[i,j] = gamma_yy[i,j] + dt * gamma_yy_dt
            K_new[i,j] = K[i,j] + dt * K_dt
            
    return chi_new, gamma_xx_new, gamma_xy_new, gamma_yy_new, K_new

class NumericalRelativitySolver:
    def __init__(self, nx=100, ny=100, dx=0.1, dy=0.1, dt=0.01):
        self.nx = nx
        self.ny = ny
        self.dx = dx
        self.dy = dy
        self.dt = dt
        
        # Grid setup
        self.x = np.linspace(-5, 5, nx)
        self.y = np.linspace(-5, 5, ny)
        self.X, self.Y = np.meshgrid(self.x, self.y)
        
        # Initialize fields
        self.initialize_fields()
    
    def initialize_fields(self):
        """Initialize the BSSN variables"""
        self.chi = np.ones((self.nx, self.ny))
        self.gamma_xx = np.ones((self.nx, self.ny))
        self.gamma_xy = np.zeros((self.nx, self.ny))
        self.gamma_yy = np.ones((self.nx, self.ny))
        self.K = np.zeros((self.nx, self.ny))
        self.A_xx = np.zeros((self.nx, self.ny))
        self.A_xy = np.zeros((self.nx, self.ny))
        self.A_yy = np.zeros((self.nx, self.ny))
        self.alpha = np.ones((self.nx, self.ny))
        self.beta_x = np.zeros((self.nx, self.ny))
        self.beta_y = np.zeros((self.nx, self.ny))
        
        self.setup_binary_black_holes()
    
    def setup_binary_black_holes(self):
        """Set up initial data for binary black holes"""
        M1 = 1.0
        M2 = 1.0
        d = 2.0
        
        x1, y1 = -d/2, 0
        x2, y2 = d/2, 0
        
        # Brill-Lindquist initial data
        for i in range(self.nx):
            for j in range(self.ny):
                r1 = np.sqrt((self.X[i,j] - x1)**2 + (self.Y[i,j] - y1)**2)
                r2 = np.sqrt((self.X[i,j] - x2)**2 + (self.Y[i,j] - y2)**2)
                
                if r1 < 0.1: r1 = 0.1  # Avoid singularity
                if r2 < 0.1: r2 = 0.1
                
                self.chi[i,j] = 1.0 + M1/(2*r1) + M2/(2*r2)
                self.alpha[i,j] = 1.0 / self.chi[i,j]**2
    
    def update_gauge(self):
        """Update gauge conditions"""
        # 1+log slicing
        self.alpha += self.dt * (-2 * self.alpha * self.K)
        
        # Gamma-driver shift (simplified)
        self.beta_x += self.dt * 0.75 * self.alpha * np.gradient(self.gamma_xx, self.dx, axis=0)
        self.beta_y += self.dt * 0.75 * self.alpha * np.gradient(self.gamma_yy, self.dy, axis=1)
    
    def evolve_BSSN(self):
        """Evolve the BSSN equations one timestep"""
        # Evolve fields using Numba-optimized function
        (self.chi, self.gamma_xx, self.gamma_xy, self.gamma_yy, self.K) = evolve_fields(
            self.chi, self.gamma_xx, self.gamma_xy, self.gamma_yy,
            self.K, self.A_xx, self.A_xy, self.A_yy,
            self.alpha, self.beta_x, self.beta_y,
            self.dx, self.dy, self.dt
        )
        
        # Update gauge conditions
        self.update_gauge()
        
        # Apply boundary conditions
        self.apply_boundary_conditions()
    
    def apply_boundary_conditions(self):
        """Apply outer boundary conditions"""
        # Simple copy boundary conditions
        self.chi[:, 0] = self.chi[:, 1]
        self.chi[:, -1] = self.chi[:, -2]
        self.chi[0, :] = self.chi[1, :]
        self.chi[-1, :] = self.chi[-2, :]
        
        # Apply to other fields similarly
        fields = [self.gamma_xx, self.gamma_xy, self.gamma_yy, 
                 self.K, self.alpha, self.beta_x, self.beta_y]
        
        for field in fields:
            field[:, 0] = field[:, 1]
            field[:, -1] = field[:, -2]
            field[0, :] = field[1, :]
            field[-1, :] = field[-2, :]
    
    def get_horizon_locations(self):
        """Find apparent horizons"""
        local_max = maximum_filter(self.chi, size=3) == self.chi
        maxima = np.where(local_max & (self.chi > 1.5))
        return list(zip(self.X[maxima], self.Y[maxima]))

def create_animation(solver, num_frames=200):
    fig, ax = plt.subplots(figsize=(10, 10))
    
    def update(frame):
        ax.clear()
        solver.evolve_BSSN()
        
        contour = ax.contourf(solver.X, solver.Y, solver.chi, 
                            levels=np.linspace(1, 2, 20), cmap='viridis')
        
        horizons = solver.get_horizon_locations()
        for x, y in horizons:
            ax.plot(x, y, 'ko', markersize=10)
        
        ax.set_xlim(-5, 5)
        ax.set_ylim(-5, 5)
        ax.set_title(f'Time = {frame * solver.dt:.2f}')
        
        return contour,
    
    anim = FuncAnimation(fig, update, frames=num_frames, interval=50, blit=True)
    plt.close()
    return anim

# Run simulation
solver = NumericalRelativitySolver()
animation = create_animation(solver)

# To save animation (optional):
# animation.save('numerical_relativity.gif', writer='pillow')

# To display in Jupyter notebook:
# from IPython.display import HTML
HTML(animation.to_jshtml())

In [12]:
import numpy as np
from scipy.ndimage import maximum_filter
import numba

class bbh:
    t = 0
    def __init__(self, nx=100, ny=100, dx=0.1, dy=0.1, dt=0.01):
        self.nx = nx
        self.ny = ny
        self.dx = dx
        self.dy = dy
        self.dt = dt
        
        # Initialize fields and setup grid
        self.x = np.linspace(-5, 5, nx)
        self.y = np.linspace(-5, 5, ny)
        self.X, self.Y = np.meshgrid(self.x, self.y)
        self.initialize_fields()
        self.t = 0

    def initialize_fields(self):
        """Initialize the BSSN variables with orbital motion"""
        self.chi = np.ones((self.nx, self.ny))
        self.gamma_xx = np.ones((self.nx, self.ny))
        self.gamma_xy = np.zeros((self.nx, self.ny))
        self.gamma_yy = np.ones((self.nx, self.ny))
        self.K = np.zeros((self.nx, self.ny))
        self.A_xx = np.zeros((self.nx, self.ny))
        self.A_xy = np.zeros((self.nx, self.ny))
        self.A_yy = np.zeros((self.nx, self.ny))
        self.alpha = np.ones((self.nx, self.ny))
        self.beta_x = np.zeros((self.nx, self.ny))
        self.beta_y = np.zeros((self.nx, self.ny))
        
        self.setup_binary_black_holes()
        
    def setup_binary_black_holes(self):
        """Set up initial data for binary black holes with orbital motion"""
        M1 = 1.0
        M2 = 1.0
        d = 2.0  # Initial separation
        
        # Initial orbital angular velocity (Kepler approximation)
        omega = np.sqrt((M1 + M2) / d**3)
        
        # Set up initial positions and momenta
        for i in range(self.nx):
            for j in range(self.ny):
                # Calculate positions relative to origin
                x = self.X[i,j]
                y = self.Y[i,j]
                
                # Rotating coordinate positions of the black holes
                x1 = -d/2 * np.cos(self.t * omega)
                y1 = -d/2 * np.sin(self.t * omega)
                x2 = d/2 * np.cos(self.t * omega)
                y2 = d/2 * np.sin(self.t * omega)
                
                # Calculate distances to both black holes
                r1 = np.sqrt((x - x1)**2 + (y - y1)**2)
                r2 = np.sqrt((x - x2)**2 + (y - y2)**2)
                
                # Avoid singularities
                r1 = max(r1, 0.1)
                r2 = max(r2, 0.1)
                
                # Conformal factor (Brill-Lindquist with momentum)
                self.chi[i,j] = 1.0 + M1/(2*r1) + M2/(2*r2)
                
                # Initial lapse
                self.alpha[i,j] = 1.0 / self.chi[i,j]**2
                
                # Initial shift (orbital motion)
                self.beta_x[i,j] = -omega * y
                self.beta_y[i,j] = omega * x
                
                # Initial extrinsic curvature for orbital motion
                r = np.sqrt(x**2 + y**2)
                if r > 0.2:
                    self.K[i,j] = -omega * (x * self.beta_y[i,j] - y * self.beta_x[i,j]) / r**2
                    
                    # Add momentum terms to A_ij
                    self.A_xx[i,j] = omega * (x * y) / r**2
                    self.A_xy[i,j] = -omega * (x**2 - y**2) / (2 * r**2)
                    self.A_yy[i,j] = -self.A_xx[i,j]
    
    def update_gauge(self):
        """Update gauge conditions"""
        # Modified 1+log slicing with orbital terms
        alpha_dx = np.gradient(self.alpha, self.dx, axis=0)
        alpha_dy = np.gradient(self.alpha, self.dy, axis=1)
        
        self.alpha += self.dt * (
            -2 * self.alpha * self.K +
            self.beta_x * alpha_dx +
            self.beta_y * alpha_dy
        )
        
        # Gamma-driver shift with orbital terms
        self.beta_x += self.dt * (
            0.75 * self.alpha * np.gradient(self.gamma_xx, self.dx, axis=0) +
            0.25 * np.gradient(self.beta_x, self.dx, axis=0)
        )
        self.beta_y += self.dt * (
            0.75 * self.alpha * np.gradient(self.gamma_yy, self.dy, axis=1) +
            0.25 * np.gradient(self.beta_y, self.dy, axis=1)
        )
        
    def evolve_BSSN(self):
        # Update time and evolve fields
        self.t += self.dt
        self.chi, self.gamma_xx, self.gamma_xy, self.gamma_yy, self.K = evolve_fields(
            self.chi, self.gamma_xx, self.gamma_xy, self.gamma_yy,
            self.K, self.A_xx, self.A_xy, self.A_yy,
            self.alpha, self.beta_x, self.beta_y,
            self.dx, self.dy, self.dt
        )
        self.update_gauge()
        self.apply_boundary_conditions()
        self.setup_binary_black_holes()
    
    def apply_boundary_conditions(self):
        # Implementing boundary conditions
        fields = [self.chi, self.gamma_xx, self.gamma_xy, self.gamma_yy,
                 self.K, self.alpha, self.beta_x, self.beta_y]
        for field in fields:
            field[:, 0] = field[:, 1]
            field[:, -1] = field[:, -2]
            field[0, :] = field[1, :]
            field[-1, :] = field[-2, :]
    
    def get_horizon_locations(self):
        # Detecting apparent horizons
        local_max = maximum_filter(self.chi, size=3) == self.chi
        maxima = np.where(local_max & (self.chi > 1.5))
        return list(zip(self.X[maxima], self.Y[maxima]))


# Initialize solver and create animation
solver = bbh(nx=int(1e3), ny=int(1e3))
animation = create_animation(solver)
animation.save("binary_black_hole_simulation.mp4", writer="ffmpeg")



KeyboardInterrupt



In [2]:
def create_animation(solver, num_frames=200):
    fig, ax = plt.subplots(figsize=(10, 10))
    def update(frame):
        ax.clear()
        solver.evolve_BSSN()
        
        # Plot conformal factor and horizons
        contour = ax.contourf(solver.X, solver.Y, solver.chi, 
                            levels=np.linspace(1, 2, 20), cmap='viridis')
        
        horizons = solver.get_horizon_locations()
        for x, y in horizons:
            ax.plot(x, y, 'ko', markersize=10)
        
        ax.set_xlim(-5, 5)
        ax.set_ylim(-5, 5)
        ax.set_title(f'Time = {solver.t:.2f}')
        
        return contour,

    anim = FuncAnimation(fig, update, frames=num_frames, interval=50, blit=True)
    plt.close()
    return anim


In [8]:
@numba.jit(nopython=True)
def compute_christoffel_symbols(gamma_xx, gamma_xy, gamma_yy, dx, dy):
    """Compute Christoffel symbols using Numba"""
    nx, ny = gamma_xx.shape
    
    # Preallocate arrays for derivatives
    gamma_xx_dx = np.zeros_like(gamma_xx)
    gamma_xy_dx = np.zeros_like(gamma_xx)
    gamma_yy_dx = np.zeros_like(gamma_xx)
    gamma_xx_dy = np.zeros_like(gamma_xx)
    gamma_xy_dy = np.zeros_like(gamma_xx)
    gamma_yy_dy = np.zeros_like(gamma_xx)
    
    # Compute derivatives using finite differences
    for i in range(1, nx-1):
        for j in range(ny):
            gamma_xx_dx[i,j] = (gamma_xx[i+1,j] - gamma_xx[i-1,j]) / (2*dx)
            gamma_xy_dx[i,j] = (gamma_xy[i+1,j] - gamma_xy[i-1,j]) / (2*dx)
            gamma_yy_dx[i,j] = (gamma_yy[i+1,j] - gamma_yy[i-1,j]) / (2*dx)
            
    for i in range(nx):
        for j in range(1, ny-1):
            gamma_xx_dy[i,j] = (gamma_xx[i,j+1] - gamma_xx[i,j-1]) / (2*dy)
            gamma_xy_dy[i,j] = (gamma_xy[i,j+1] - gamma_xy[i,j-1]) / (2*dy)
            gamma_yy_dy[i,j] = (gamma_yy[i,j+1] - gamma_yy[i,j-1]) / (2*dy)
    
    return gamma_xx_dx, gamma_xy_dx, gamma_yy_dx, gamma_xx_dy, gamma_xy_dy, gamma_yy_dy

@numba.jit(nopython=True)
def evolve_fields(chi, gamma_xx, gamma_xy, gamma_yy, K, A_xx, A_xy, A_yy, 
                 alpha, beta_x, beta_y, dx, dy, dt):
    """Evolve BSSN fields one timestep using Numba"""
    nx, ny = chi.shape
    
    # Preallocate arrays for new values
    chi_new = np.copy(chi)
    gamma_xx_new = np.copy(gamma_xx)
    gamma_xy_new = np.copy(gamma_xy)
    gamma_yy_new = np.copy(gamma_yy)
    K_new = np.copy(K)
    A_xx_new = np.copy(A_xx)
    A_xy_new = np.copy(A_xy)
    A_yy_new = np.copy(A_yy)
    
    # Compute derivatives
    for i in range(1, nx-1):
        for j in range(1, ny-1):
            # Compute derivatives
            chi_dx = (chi[i+1,j] - chi[i-1,j]) / (2*dx)
            chi_dy = (chi[i,j+1] - chi[i,j-1]) / (2*dy)
            
            beta_x_dx = (beta_x[i+1,j] - beta_x[i-1,j]) / (2*dx)
            beta_y_dy = (beta_y[i,j+1] - beta_y[i,j-1]) / (2*dy)
            
            # Evolution equations
            # Modified chi evolution with momentum terms
            chi_dt = (2.0/3.0) * chi[i,j] * (
                alpha[i,j] * K[i,j] - 
                beta_x_dx - beta_y_dy +
                beta_x[i,j] * chi_dx + beta_y[i,j] * chi_dy
            )
            
            # Modified conformal metric evolution with momentum terms
            gamma_xx_dt = (-2 * alpha[i,j] * A_xx[i,j] + 
                         beta_x[i,j] * (gamma_xx[i+1,j] - gamma_xx[i-1,j]) / (2*dx) +
                         beta_y[i,j] * (gamma_xx[i,j+1] - gamma_xx[i,j-1]) / (2*dy))
            
            gamma_xy_dt = (-2 * alpha[i,j] * A_xy[i,j] +
                         beta_x[i,j] * (gamma_xy[i+1,j] - gamma_xy[i-1,j]) / (2*dx) +
                         beta_y[i,j] * (gamma_xy[i,j+1] - gamma_xy[i,j-1]) / (2*dy))
            
            gamma_yy_dt = (-2 * alpha[i,j] * A_yy[i,j] +
                         beta_x[i,j] * (gamma_yy[i+1,j] - gamma_yy[i-1,j]) / (2*dx) +
                         beta_y[i,j] * (gamma_yy[i,j+1] - gamma_yy[i,j-1]) / (2*dy))
            
            # Evolution equation for K with momentum terms
            K_dt = (alpha[i,j] * (A_xx[i,j]**2 + 2*A_xy[i,j]**2 + A_yy[i,j]**2) -
                   alpha[i,j] * K[i,j]**2/3 +
                   beta_x[i,j] * (K[i+1,j] - K[i-1,j]) / (2*dx) +
                   beta_y[i,j] * (K[i,j+1] - K[i,j-1]) / (2*dy))
            
            # Update fields
            chi_new[i,j] = chi[i,j] + dt * chi_dt
            gamma_xx_new[i,j] = gamma_xx[i,j] + dt * gamma_xx_dt
            gamma_xy_new[i,j] = gamma_xy[i,j] + dt * gamma_xy_dt
            gamma_yy_new[i,j] = gamma_yy[i,j] + dt * gamma_yy_dt
            K_new[i,j] = K[i,j] + dt * K_dt
            
    return chi_new, gamma_xx_new, gamma_xy_new, gamma_yy_new, K_new


In [10]:
import numpy as np

class NumericalRelativitySolver:
    def __init__(self, nx=100, ny=100, dx=0.1, dy=0.1, dt=0.01):
        # Grid properties
        self.nx = nx
        self.ny = ny
        self.dx = dx
        self.dy = dy
        self.dt = dt
        self.t = 0  # Start time at 0

        # Generate the grid
        self.x = np.linspace(-5, 5, nx)
        self.y = np.linspace(-5, 5, ny)
        self.X, self.Y = np.meshgrid(self.x, self.y)
        
        # Initialize fields
        self.field = np.exp(-self.X**2 - self.Y**2)  # Example Gaussian field
        self.field_velocity = np.zeros_like(self.field)

    def update(self):
        # Simple wave-like update (replace with Einstein's equations for more complexity)
        laplacian = (
            (np.roll(self.field, 1, axis=0) - 2*self.field + np.roll(self.field, -1, axis=0)) / self.dx**2 +
            (np.roll(self.field, 1, axis=1) - 2*self.field + np.roll(self.field, -1, axis=1)) / self.dy**2
        )
        
        # Update velocity and field with a simple wave equation
        self.field_velocity += self.dt * laplacian
        self.field += self.dt * self.field_velocity
        
        # Increment time
        self.t += self.dt

    def run(self, steps=100):
        # Run the solver for a given number of steps
        for _ in range(steps):
            self.update()
        return self.field

# Usage
solver = NumericalRelativitySolver()
final_state = solver.run(steps=100)
print("Final field state at t =", solver.t)


Final field state at t = 1.0000000000000007


In [9]:
from newbbh import *
# Example 1: Equal mass binary black holes
def run_equal_mass_simulation():
    # Set up parameters for equal mass case
    params = SimulationParameters(
        M1=1.0,
        M2=1.0,
        d=3.0,
        nx=200,
        ny=200,
        dt=0.1,
        x_min=-10,
        x_max=10,
        y_min=-10,
        y_max=10
    )
    
    # Create solver and animation
    solver = ImprovedBBH(params)
    anim = create_improved_animation(solver, num_frames=1000)
    
    # Save animation
    anim.save('equal_mass_merger.mp4', writer='ffmpeg', fps=30)

# Example 2: Unequal mass binary black holes
def run_unequal_mass_simulation():
    # Set up parameters for unequal mass case (3:1 mass ratio)
    params = SimulationParameters(
        M1=1.5,
        M2=0.5,
        d=4.0,  # Slightly larger separation
        nx=200,
        ny=200,
        dt=0.008,  # Slightly smaller timestep for stability
        x_min=-12,
        x_max=12,
        y_min=-12,
        y_max=12
    )
    
    # Create solver and animation
    solver = ImprovedBBH(params)
    
    anim = create_improved_animation(solver, num_frames=400)
    
    # Save animation
    anim.save('unequal_mass_merger.mp4', writer='ffmpeg', fps=30)


In [10]:
run_equal_mass_simulation()

In [3]:
run_unequal_mass_simulation()